## regex: IBAN oder ISBN?

[IBAN](https://de.wikipedia.org/wiki/Internationale_Bankkontonummer)

* zwei Großbuchstaben
* zwei Prüfziffern
* bis zu 30 Ziffern, nach belieben durch Leerzeichen getrennt
* z.B. `DE07 1234 1234 1234 1234 12`

[ISBN-13 mit Trennstrichen](https://de.wikipedia.org/wiki/Internationale_Standardbuchnummer)
* Präfix–Gruppennummer–Verlagsnummer–Titelnummer–Prüfziffer
* z.B. `978-3-86680-192-9`
    

In [1]:
import re

In [2]:
# Quelle: https://stackoverflow.com/questions/56520050/how-to-get-matched-word-from-regex-match-object-after-using-finditer

regex = r"""
(?P<isbn> \d+-\d+-\d+-\d+-\d)
| (?P<iban> 
[A-Z]{2}  # zwei Großbuchstaben
\d{2}     # zwei Prüfziffen
[\d ]{4,30} # 4 bis 30 Ziffern
\W  # eine Wortgrenze
)
"""

test_str = ("Falls die Überweisung für das Buch 978-3-86680-192-9 auf \n"
    "DE07 1234 1234 1234 1234 12 nicht klappt, bitte \n"
    "einfach Rosi unter 089 / 32 16 8 anrufen!\n")

matches = re.finditer(regex, test_str, re.MULTILINE  | re.VERBOSE)

for matchNum, match in enumerate(matches, start=1):
    
    print (f"""\nMatch {matchNum} was found at """
           f"""{match.start()}-{match.end()}: """
           f"""{match.group()}""")
    
    for groupNum in range(0, len(match.groups())):
        groupNum = groupNum + 1
        print (f"""    Group {groupNum} found at {match.start(groupNum)}-{match.end(groupNum)}: """
               f"""{match.group(groupNum)}""")


Match 1 was found at 35-52: 978-3-86680-192-9
    Group 1 found at 35-52: 978-3-86680-192-9
    Group 2 found at -1--1: None

Match 2 was found at 58-86: DE07 1234 1234 1234 1234 12 
    Group 1 found at -1--1: None
    Group 2 found at 58-86: DE07 1234 1234 1234 1234 12 


In [3]:
regex_dict = { "ISBN": r"\d+-\d+-\d+-\d+-\d",
     "IBAN": r"[A-Z]{2}\d{2}[\d ]{4,30}",
     "TEL": r"\d+\s*[-/]\s*[\d ]+"}

regex = "|".join([ f"(?P<{k}>{v} )" for k,v in regex_dict.items()])
regex

'(?P<ISBN>\\d+-\\d+-\\d+-\\d+-\\d )|(?P<IBAN>[A-Z]{2}\\d{2}[\\d ]{4,30} )|(?P<TEL>\\d+\\s*[-/]\\s*[\\d ]+ )'

In [4]:
test_str = ("Falls die Überweisung für das Buch 978-3-86680-192-9 auf \n"
    "DE07 1234 1234 1234 1234 12 nicht klappt, bitte \n"
    "einfach Rosi unter 089 / 32 16 8 anrufen!\n")


def substfn(match):
    match_dict = {k: f"{match.group(k)} ({k})" for  k in regex_dict.keys() if match.group(k) != None}
    print(match_dict)
    return " ".join(match_dict.values())
    
# You can manually specify the number of replacements by changing the 4th argument
result = re.sub(regex, substfn, test_str, 0, re.MULTILINE | re.VERBOSE)

if result:
    print ("\n", result)


{'ISBN': '978-3-86680-192-9 (ISBN)'}
{'IBAN': 'DE07 1234 1234 1234 1234 12  (IBAN)'}
{'TEL': '089 / 32 16 8  (TEL)'}

 Falls die Überweisung für das Buch 978-3-86680-192-9 (ISBN) auf 
DE07 1234 1234 1234 1234 12  (IBAN)nicht klappt, bitte 
einfach Rosi unter 089 / 32 16 8  (TEL)anrufen!

